Install and import library modules. Download English stopwords and WordNet. Set logging to INFO

In [1]:
import sys
!{sys.executable} -m pip install gensim
!{sys.executable} -m pip install pyLDAvis
!{sys.executable} -m pip install pandas
!{sys.executable} -m pip install numpy
!{sys.executable} -m pip install matplotlib
!{sys.executable} -m pip install nltk

import re, gensim, pyLDAvis, logging, datetime, multiprocessing, os, pickle
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from math import floor, ceil
from nltk.corpus import stopwords
from nltk import download
from nltk.stem import WordNetLemmatizer

download('stopwords')
download('wordnet')

logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

You should consider upgrading via the '/usr/local/Cellar/jupyterlab/2.1.2/libexec/bin/python3.8 -m pip install --upgrade pip' command.
You should consider upgrading via the '/usr/local/Cellar/jupyterlab/2.1.2/libexec/bin/python3.8 -m pip install --upgrade pip' command.
You should consider upgrading via the '/usr/local/Cellar/jupyterlab/2.1.2/libexec/bin/python3.8 -m pip install --upgrade pip' command.
You should consider upgrading via the '/usr/local/Cellar/jupyterlab/2.1.2/libexec/bin/python3.8 -m pip install --upgrade pip' command.
You should consider upgrading via the '/usr/local/Cellar/jupyterlab/2.1.2/libexec/bin/python3.8 -m pip install --upgrade pip' command.
You should consider upgrading via the '/usr/local/Cellar/jupyterlab/2.1.2/libexec/bin/python3.8 -m pip install --upgrade pip' command.


[nltk_data] Downloading package stopwords to /Users/joost/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /Users/joost/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Read the data as pandas dataframe, remove items with missing abstracts, and fill other missing data with empty strings

In [2]:
df = pd.read_csv('data_merged_and_filtered.csv')
df = df[df['abstract'].notna()]
df.fillna("", inplace=True)

Combine the text fiels into one

In [3]:
df["data"] = df["abstract"] + " " + df["keywords"] + " " + df["title"]

2021-04-19 09:55:40,042 : INFO : NumExpr defaulting to 8 threads.


Remove copyright notices from the text

In [4]:
copyright_re = "(©|&#x00A9;|Copyright)(.*?(?=B\\.V\\.|Ltd|\\.))(B\\.V\\.|Ltd|\\.)"
rights = "All rights reserved."
df.replace(copyright_re, '', regex=True, inplace=True)
df.replace(rights, '', regex=False, inplace=True)

Tokenize, convert to lowercase, remove punctuation, remove stop-words, lemmatize

In [5]:
def preprocess(text):
  result = [word for word in gensim.utils.simple_preprocess(text, deacc=True) if word not in stop_words]
  wordnet_lemmatizer = WordNetLemmatizer()
  result = [wordnet_lemmatizer.lemmatize(word) for word in result]
  return result

stop_words = stopwords.words('english')
df["data_preprocessed"] = df["data"].map(preprocess)

Generate the Dictionairy and perform relative pruning

In [6]:
dictionary = gensim.corpora.Dictionary(df["data_preprocessed"])
dictionary.filter_extremes(no_below=(floor(0.005 * len(df))), no_above=0.99)

2021-04-19 09:57:50,857 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2021-04-19 09:57:52,267 : INFO : adding document #10000 to Dictionary(27074 unique tokens: ['ability', 'acceptable', 'additionally', 'analysis', 'anti']...)
2021-04-19 09:57:53,612 : INFO : adding document #20000 to Dictionary(38089 unique tokens: ['ability', 'acceptable', 'additionally', 'analysis', 'anti']...)
2021-04-19 09:57:54,928 : INFO : adding document #30000 to Dictionary(46717 unique tokens: ['ability', 'acceptable', 'additionally', 'analysis', 'anti']...)
2021-04-19 09:57:56,197 : INFO : adding document #40000 to Dictionary(53696 unique tokens: ['ability', 'acceptable', 'additionally', 'analysis', 'anti']...)
2021-04-19 09:57:57,429 : INFO : adding document #50000 to Dictionary(59648 unique tokens: ['ability', 'acceptable', 'additionally', 'analysis', 'anti']...)
2021-04-19 09:57:58,643 : INFO : adding document #60000 to Dictionary(64997 unique tokens: ['ability', 'acceptable', 'additional

Make the bag of words

In [7]:
corpus = [dictionary.doc2bow(doc) for doc in df["data_preprocessed"]]

Generate all models for evaluation

In [8]:
k = [36] #[1, 4, 9, 16, 25, 36, 49, 64, 81, 100, 121, 144, 169, 196, 225, 256, 289, 324, 361] #later added [30, 40, 42]
random_states = [24, 1024] #later added [27, 1027]

texts = df["data_preprocessed"]
chunksize = ceil(len(texts))
passes = 20
iterations = 100
eval_every = None
dir_prior = 'auto'

for random_state in random_states:
    for num_topics in k:
        
        name = "rs{}k{}".format(random_state, num_topics)
        
        
        if 'model_' + name in os.listdir('models'):
            print(datetime.datetime.now().strftime('%H:%M:%S') + ' Model ' + name + ' already in directory. Skipped')
        
        else:
            print(datetime.datetime.now().strftime('%H:%M:%S') + " Building model " + name)
            lda_model = gensim.models.LdaModel(corpus, num_topics=num_topics, id2word=dictionary, alpha=dir_prior, eta=dir_prior, random_state=random_state, chunksize=chunksize, passes=passes, iterations=iterations)

            lda_model.save(os.path.join('models', 'model_' + name))

2021-04-19 09:58:06,995 : INFO : using autotuned alpha, starting with [0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778, 0.027777778]
2021-04-19 09:58:06,997 : INFO : using serial LDA version on this node
2021-04-19 09:58:07,007 : INFO : running online (multi-pass) LDA training, 36 topics, 20 passes over the supplied corpus of 79433 documents, updating model once every 79433 documents, evaluating perplexity every 79433 documents, iterating 100x with a convergence threshold of 0.001000


09:58:06 Building model rs24k36


2021-04-19 10:00:53,815 : INFO : -8.459 per-word bound, 351.8 perplexity estimate based on a held-out corpus of 79433 documents with 7925243 words
2021-04-19 10:00:53,816 : INFO : PROGRESS: pass 0, at document #79433/79433
2021-04-19 10:02:50,392 : INFO : optimized alpha [0.024740206, 0.024995511, 0.02546044, 0.02545825, 0.024693657, 0.028436383, 0.025288315, 0.02610419, 0.02687848, 0.024658537, 0.02500476, 0.024150953, 0.024295676, 0.024595633, 0.025964715, 0.025051627, 0.02556773, 0.025108878, 0.02433295, 0.025015086, 0.029708583, 0.02430077, 0.025682138, 0.025561495, 0.02529584, 0.026193064, 0.024758613, 0.026637029, 0.024948988, 0.024816198, 0.02800215, 0.025401901, 0.024494616, 0.026145807, 0.026432889, 0.026630918]
2021-04-19 10:02:50,402 : INFO : topic #11 (0.024): 0.032*"data" + 0.016*"network" + 0.014*"privacy" + 0.007*"computing" + 0.007*"security" + 0.007*"care" + 0.006*"service" + 0.006*"result" + 0.006*"based" + 0.006*"social"
2021-04-19 10:02:50,403 : INFO : topic #12 (0.

2021-04-19 10:15:37,694 : INFO : topic #11 (0.020): 0.042*"sensor" + 0.025*"data" + 0.025*"network" + 0.020*"energy" + 0.018*"memory" + 0.014*"adolescent" + 0.013*"detection" + 0.012*"fall" + 0.012*"multimedia" + 0.010*"privacy"
2021-04-19 10:15:37,696 : INFO : topic #25 (0.021): 0.044*"privacy" + 0.017*"protocol" + 0.015*"knowledge" + 0.013*"proof" + 0.012*"party" + 0.011*"zero" + 0.009*"security" + 0.009*"data" + 0.008*"user" + 0.006*"two"
2021-04-19 10:15:37,697 : INFO : topic #6 (0.025): 0.080*"data" + 0.017*"research" + 0.016*"privacy" + 0.011*"protection" + 0.010*"personal" + 0.009*"big" + 0.008*"use" + 0.007*"study" + 0.007*"learning" + 0.006*"technology"
2021-04-19 10:15:37,699 : INFO : topic #20 (0.026): 0.076*"privacy" + 0.067*"data" + 0.014*"policy" + 0.012*"preserving" + 0.011*"model" + 0.011*"based" + 0.009*"protection" + 0.009*"method" + 0.008*"information" + 0.008*"user"
2021-04-19 10:15:37,700 : INFO : topic #5 (0.026): 0.088*"data" + 0.038*"cloud" + 0.026*"privacy" + 0

2021-04-19 10:26:38,733 : INFO : topic #10 (0.026): 0.039*"social" + 0.025*"privacy" + 0.020*"medium" + 0.013*"study" + 0.011*"use" + 0.009*"people" + 0.009*"student" + 0.009*"information" + 0.009*"self" + 0.008*"research"
2021-04-19 10:26:38,734 : INFO : topic #16 (0.026): 0.049*"user" + 0.040*"privacy" + 0.030*"service" + 0.028*"system" + 0.026*"web" + 0.015*"context" + 0.015*"information" + 0.013*"agent" + 0.010*"based" + 0.008*"paper"
2021-04-19 10:26:38,735 : INFO : topic diff=0.201253, rho=0.316228
2021-04-19 10:27:59,463 : INFO : -6.539 per-word bound, 93.0 perplexity estimate based on a held-out corpus of 79433 documents with 7925243 words
2021-04-19 10:27:59,464 : INFO : PROGRESS: pass 9, at document #79433/79433
2021-04-19 10:28:59,189 : INFO : optimized alpha [0.02514195, 0.021839015, 0.021250376, 0.02407234, 0.021857092, 0.025375327, 0.025321046, 0.020341123, 0.022415685, 0.022494003, 0.025843564, 0.019655451, 0.022276647, 0.025418524, 0.020322347, 0.023003574, 0.026634347,

...

2021-04-19 10:53:37,954 : INFO : -8.461 per-word bound, 352.3 perplexity estimate based on a held-out corpus of 79433 documents with 7925243 words
2021-04-19 10:53:37,955 : INFO : PROGRESS: pass 0, at document #79433/79433
2021-04-19 10:55:28,033 : INFO : optimized alpha [0.02548813, 0.026145909, 0.024299687, 0.02732004, 0.024242733, 0.02526844, 0.025871027, 0.024352036, 0.025829757, 0.026516449, 0.025694316, 0.02431365, 0.02598808, 0.025419345, 0.025516225, 0.025891263, 0.026122767, 0.026815338, 0.026203863, 0.027316514, 0.025686327, 0.025743444, 0.025485836, 0.025786713, 0.02532385, 0.027736565, 0.026202237, 0.024852451, 0.024831759, 0.027241869, 0.0243578, 0.024594724, 0.024584185, 0.02422279, 0.024415556, 0.02575808]
2021-04-19 10:55:28,039 : INFO : topic #33 (0.024): 0.021*"data" + 0.016*"scheme" + 0.014*"security" + 0.011*"privacy" + 0.010*"based" + 0.007*"authentication" + 0.006*"paper" + 0.006*"secure" + 0.006*"system" + 0.006*"proposed"
2021-04-19 10:55:28,039 : INFO : topic #

2021-04-19 11:07:39,882 : INFO : topic #4 (0.021): 0.035*"energy" + 0.034*"smart" + 0.017*"privacy" + 0.014*"grid" + 0.014*"power" + 0.012*"system" + 0.011*"consumption" + 0.011*"demand" + 0.010*"meter" + 0.009*"consumer"
2021-04-19 11:07:39,883 : INFO : topic #9 (0.021): 0.037*"data" + 0.031*"learning" + 0.026*"privacy" + 0.017*"analytics" + 0.012*"spectrum" + 0.009*"big" + 0.009*"cloud" + 0.009*"paper" + 0.008*"system" + 0.007*"information"
2021-04-19 11:07:39,884 : INFO : topic #29 (0.026): 0.050*"social" + 0.048*"user" + 0.037*"network" + 0.037*"privacy" + 0.017*"information" + 0.013*"online" + 0.011*"sharing" + 0.011*"data" + 0.010*"based" + 0.009*"mobile"
2021-04-19 11:07:39,885 : INFO : topic #25 (0.026): 0.058*"data" + 0.051*"privacy" + 0.026*"information" + 0.022*"protection" + 0.015*"personal" + 0.014*"right" + 0.010*"security" + 0.010*"technology" + 0.009*"law" + 0.008*"regulation"
2021-04-19 11:07:39,886 : INFO : topic #6 (0.028): 0.102*"data" + 0.039*"privacy" + 0.014*"min

2021-04-19 11:17:21,876 : INFO : topic #32 (0.025): 0.020*"privacy" + 0.019*"study" + 0.018*"risk" + 0.012*"survey" + 0.012*"result" + 0.011*"testing" + 0.011*"participant" + 0.010*"information" + 0.009*"attitude" + 0.008*"concern"
2021-04-19 11:17:21,877 : INFO : topic #25 (0.026): 0.074*"data" + 0.056*"privacy" + 0.029*"protection" + 0.027*"information" + 0.020*"personal" + 0.013*"right" + 0.011*"regulation" + 0.009*"law" + 0.009*"technology" + 0.008*"security"
2021-04-19 11:17:21,878 : INFO : topic #6 (0.029): 0.107*"data" + 0.040*"privacy" + 0.018*"mining" + 0.015*"preserving" + 0.014*"method" + 0.013*"algorithm" + 0.012*"sensitive" + 0.012*"information" + 0.009*"technique" + 0.009*"anonymization"
2021-04-19 11:17:21,879 : INFO : topic diff=0.187791, rho=0.316228
2021-04-19 11:18:41,589 : INFO : -6.531 per-word bound, 92.5 perplexity estimate based on a held-out corpus of 79433 documents with 7925243 words
2021-04-19 11:18:41,590 : INFO : PROGRESS: pass 9, at document #79433/79433


2021-04-19 11:26:21,582 : INFO : topic #6 (0.030): 0.111*"data" + 0.041*"privacy" + 0.020*"mining" + 0.016*"preserving" + 0.015*"method" + 0.014*"algorithm" + 0.013*"sensitive" + 0.012*"information" + 0.010*"technique" + 0.010*"anonymization"
2021-04-19 11:26:21,583 : INFO : topic diff=0.237963, rho=0.267261
2021-04-19 11:27:37,702 : INFO : -6.515 per-word bound, 91.5 perplexity estimate based on a held-out corpus of 79433 documents with 7925243 words
2021-04-19 11:27:37,703 : INFO : PROGRESS: pass 13, at document #79433/79433
2021-04-19 11:28:33,548 : INFO : optimized alpha [0.023428962, 0.023682024, 0.020673456, 0.021931458, 0.019836966, 0.019315297, 0.030472701, 0.024669632, 0.02298459, 0.019480523, 0.02332955, 0.022520775, 0.02429447, 0.022066839, 0.024741765, 0.021266518, 0.019808745, 0.020320494, 0.018617187, 0.019518264, 0.02151368, 0.025339434, 0.019279191, 0.022823066, 0.022359135, 0.02730989, 0.024951726, 0.02441102, 0.019931333, 0.024378056, 0.024784846, 0.022009999, 0.02584

2021-04-19 11:35:04,384 : INFO : topic diff=0.293836, rho=0.235702
2021-04-19 11:36:21,300 : INFO : -6.509 per-word bound, 91.1 perplexity estimate based on a held-out corpus of 79433 documents with 7925243 words
2021-04-19 11:36:21,301 : INFO : PROGRESS: pass 17, at document #79433/79433
2021-04-19 11:37:14,688 : INFO : optimized alpha [0.024080964, 0.023966637, 0.020679612, 0.021887109, 0.019633343, 0.019027594, 0.03138483, 0.025590219, 0.023423195, 0.01964148, 0.023305606, 0.023223711, 0.024574276, 0.022228874, 0.026145011, 0.02086496, 0.019479517, 0.020011, 0.01824975, 0.019641194, 0.02134233, 0.026793644, 0.018757442, 0.02312292, 0.022450572, 0.02818199, 0.027528085, 0.024632003, 0.019754052, 0.024346858, 0.025407331, 0.022662932, 0.026323719, 0.026283788, 0.022591516, 0.024283368]
2021-04-19 11:37:14,695 : INFO : topic #18 (0.018): 0.067*"system" + 0.060*"healthcare" + 0.044*"recommendation" + 0.042*"collaborative" + 0.024*"privacy" + 0.021*"based" + 0.021*"filtering" + 0.018*"re

Evaluate all models present in the current directory

In [9]:
models_to_evaluate = []

for entry in os.scandir('models'):
    if entry.path.endswith('.state'):
        models_to_evaluate.append(entry.path[:-6])
        
for path in models_to_evaluate:
    model = gensim.models.LdaModel.load(path)
    coherence_model_lda = gensim.models.coherencemodel.CoherenceModel(model=model, texts=texts, dictionary=dictionary, coherence='c_v')
    coherence = coherence_model_lda.get_coherence()
        
    with open(os.path.join('models', 'scores.txt'), "a") as f:
        f.write("\"" + str(os.path.split(path)[1]) + "\"" ' : ' + str(coherence) + ',\n')   

2021-04-19 11:41:31,697 : INFO : loading LdaModel object from models/model_rs1027k25
2021-04-19 11:41:31,699 : INFO : loading expElogbeta from models/model_rs1027k25.expElogbeta.npy with mmap=None
2021-04-19 11:41:31,701 : INFO : setting ignored attribute id2word to None
2021-04-19 11:41:31,702 : INFO : setting ignored attribute state to None
2021-04-19 11:41:31,703 : INFO : setting ignored attribute dispatcher to None
2021-04-19 11:41:31,703 : INFO : loaded models/model_rs1027k25
2021-04-19 11:41:31,703 : INFO : loading LdaState object from models/model_rs1027k25.state
2021-04-19 11:41:31,707 : INFO : loaded models/model_rs1027k25.state
2021-04-19 11:41:31,714 : INFO : using ParallelWordOccurrenceAccumulator(processes=7, batch_size=64) to estimate probabilities from sliding windows
2021-04-19 11:41:32,535 : INFO : 1 batches submitted to accumulate stats from 64 documents (1275 virtual)
2021-04-19 11:41:32,549 : INFO : 2 batches submitted to accumulate stats from 128 documents (2284 vi

2021-04-19 11:41:40,128 : INFO : 70 batches submitted to accumulate stats from 4480 documents (114837 virtual)
2021-04-19 11:41:40,147 : INFO : 71 batches submitted to accumulate stats from 4544 documents (115986 virtual)
2021-04-19 11:41:40,366 : INFO : 72 batches submitted to accumulate stats from 4608 documents (118066 virtual)
2021-04-19 11:41:40,645 : INFO : 73 batches submitted to accumulate stats from 4672 documents (119187 virtual)
2021-04-19 11:41:40,743 : INFO : 74 batches submitted to accumulate stats from 4736 documents (120756 virtual)
2021-04-19 11:41:40,821 : INFO : 75 batches submitted to accumulate stats from 4800 documents (122027 virtual)
2021-04-19 11:41:40,871 : INFO : 76 batches submitted to accumulate stats from 4864 documents (124696 virtual)
2021-04-19 11:41:41,032 : INFO : 77 batches submitted to accumulate stats from 4928 documents (125619 virtual)
2021-04-19 11:41:41,044 : INFO : 78 batches submitted to accumulate stats from 4992 documents (127133 virtual)
2

2021-04-19 11:41:48,818 : INFO : 148 batches submitted to accumulate stats from 9472 documents (228811 virtual)
2021-04-19 11:41:48,906 : INFO : 149 batches submitted to accumulate stats from 9536 documents (230712 virtual)
2021-04-19 11:41:49,046 : INFO : 150 batches submitted to accumulate stats from 9600 documents (232012 virtual)
2021-04-19 11:41:49,089 : INFO : 151 batches submitted to accumulate stats from 9664 documents (233233 virtual)
2021-04-19 11:41:49,449 : INFO : 152 batches submitted to accumulate stats from 9728 documents (233853 virtual)
2021-04-19 11:41:49,561 : INFO : 153 batches submitted to accumulate stats from 9792 documents (234235 virtual)
2021-04-19 11:41:49,609 : INFO : 154 batches submitted to accumulate stats from 9856 documents (235617 virtual)
2021-04-19 11:41:49,647 : INFO : 155 batches submitted to accumulate stats from 9920 documents (237833 virtual)
2021-04-19 11:41:49,683 : INFO : 156 batches submitted to accumulate stats from 9984 documents (238949 v

2021-04-19 11:41:56,392 : INFO : 221 batches submitted to accumulate stats from 14144 documents (331093 virtual)
2021-04-19 11:41:56,414 : INFO : 222 batches submitted to accumulate stats from 14208 documents (331729 virtual)
2021-04-19 11:41:56,598 : INFO : 223 batches submitted to accumulate stats from 14272 documents (332776 virtual)
2021-04-19 11:41:56,738 : INFO : 224 batches submitted to accumulate stats from 14336 documents (334960 virtual)
2021-04-19 11:41:56,791 : INFO : 225 batches submitted to accumulate stats from 14400 documents (337035 virtual)
2021-04-19 11:41:56,808 : INFO : 226 batches submitted to accumulate stats from 14464 documents (339721 virtual)
2021-04-19 11:41:56,887 : INFO : 227 batches submitted to accumulate stats from 14528 documents (340405 virtual)
2021-04-19 11:41:57,040 : INFO : 228 batches submitted to accumulate stats from 14592 documents (341682 virtual)
2021-04-19 11:41:57,122 : INFO : 229 batches submitted to accumulate stats from 14656 documents 

2021-04-19 11:42:03,502 : INFO : 299 batches submitted to accumulate stats from 19136 documents (411759 virtual)
2021-04-19 11:42:03,524 : INFO : 300 batches submitted to accumulate stats from 19200 documents (412494 virtual)
2021-04-19 11:42:03,711 : INFO : 301 batches submitted to accumulate stats from 19264 documents (414064 virtual)
2021-04-19 11:42:03,776 : INFO : 302 batches submitted to accumulate stats from 19328 documents (414957 virtual)
2021-04-19 11:42:03,815 : INFO : 303 batches submitted to accumulate stats from 19392 documents (416038 virtual)
2021-04-19 11:42:03,918 : INFO : 304 batches submitted to accumulate stats from 19456 documents (418013 virtual)
2021-04-19 11:42:04,192 : INFO : 305 batches submitted to accumulate stats from 19520 documents (418830 virtual)
2021-04-19 11:42:04,203 : INFO : 306 batches submitted to accumulate stats from 19584 documents (419750 virtual)
2021-04-19 11:42:04,366 : INFO : 308 batches submitted to accumulate stats from 19712 documents 

...

2021-04-19 16:07:48,179 : INFO : 592 batches submitted to accumulate stats from 37888 documents (660444 virtual)
2021-04-19 16:07:49,029 : INFO : 593 batches submitted to accumulate stats from 37952 documents (660966 virtual)
2021-04-19 16:07:49,342 : INFO : 594 batches submitted to accumulate stats from 38016 documents (661996 virtual)
2021-04-19 16:07:49,378 : INFO : 595 batches submitted to accumulate stats from 38080 documents (662390 virtual)
2021-04-19 16:07:49,650 : INFO : 596 batches submitted to accumulate stats from 38144 documents (663374 virtual)
2021-04-19 16:07:50,536 : INFO : 597 batches submitted to accumulate stats from 38208 documents (665115 virtual)
2021-04-19 16:07:51,072 : INFO : 598 batches submitted to accumulate stats from 38272 documents (667294 virtual)
2021-04-19 16:07:51,278 : INFO : 599 batches submitted to accumulate stats from 38336 documents (670117 virtual)
2021-04-19 16:07:51,528 : INFO : 600 batches submitted to accumulate stats from 38400 documents 

2021-04-19 16:08:33,014 : INFO : 687 batches submitted to accumulate stats from 43968 documents (723121 virtual)
2021-04-19 16:08:33,595 : INFO : 688 batches submitted to accumulate stats from 44032 documents (727404 virtual)
2021-04-19 16:08:34,464 : INFO : 689 batches submitted to accumulate stats from 44096 documents (733302 virtual)
2021-04-19 16:08:34,931 : INFO : 690 batches submitted to accumulate stats from 44160 documents (736244 virtual)
2021-04-19 16:08:35,193 : INFO : 691 batches submitted to accumulate stats from 44224 documents (736630 virtual)
2021-04-19 16:08:35,316 : INFO : 692 batches submitted to accumulate stats from 44288 documents (736888 virtual)
2021-04-19 16:08:35,902 : INFO : 693 batches submitted to accumulate stats from 44352 documents (738297 virtual)
2021-04-19 16:08:35,967 : INFO : 694 batches submitted to accumulate stats from 44416 documents (738384 virtual)
2021-04-19 16:08:36,359 : INFO : 695 batches submitted to accumulate stats from 44480 documents 

2021-04-19 16:09:20,349 : INFO : 790 batches submitted to accumulate stats from 50560 documents (779644 virtual)
2021-04-19 16:09:21,591 : INFO : 793 batches submitted to accumulate stats from 50752 documents (779914 virtual)
2021-04-19 16:09:21,787 : INFO : 794 batches submitted to accumulate stats from 50816 documents (781153 virtual)
2021-04-19 16:09:22,430 : INFO : 795 batches submitted to accumulate stats from 50880 documents (782584 virtual)
2021-04-19 16:09:23,761 : INFO : 800 batches submitted to accumulate stats from 51200 documents (781433 virtual)
2021-04-19 16:09:24,699 : INFO : 801 batches submitted to accumulate stats from 51264 documents (782495 virtual)
2021-04-19 16:09:25,473 : INFO : 802 batches submitted to accumulate stats from 51328 documents (783175 virtual)
2021-04-19 16:09:26,355 : INFO : 805 batches submitted to accumulate stats from 51520 documents (783415 virtual)
2021-04-19 16:09:26,463 : INFO : 806 batches submitted to accumulate stats from 51584 documents 

2021-04-19 16:10:13,695 : INFO : 917 batches submitted to accumulate stats from 58688 documents (809807 virtual)
2021-04-19 16:10:14,779 : INFO : 921 batches submitted to accumulate stats from 58944 documents (808970 virtual)
2021-04-19 16:10:15,314 : INFO : 922 batches submitted to accumulate stats from 59008 documents (812437 virtual)
2021-04-19 16:10:18,112 : INFO : 930 batches submitted to accumulate stats from 59520 documents (809513 virtual)
2021-04-19 16:10:18,254 : INFO : 931 batches submitted to accumulate stats from 59584 documents (809717 virtual)
2021-04-19 16:10:19,085 : INFO : 933 batches submitted to accumulate stats from 59712 documents (809871 virtual)
2021-04-19 16:10:19,098 : INFO : 934 batches submitted to accumulate stats from 59776 documents (809975 virtual)
2021-04-19 16:10:20,530 : INFO : 936 batches submitted to accumulate stats from 59904 documents (809913 virtual)
2021-04-19 16:10:20,684 : INFO : 937 batches submitted to accumulate stats from 59968 documents 

2021-04-19 16:11:42,959 : INFO : 1165 batches submitted to accumulate stats from 74560 documents (750769 virtual)
2021-04-19 16:11:44,922 : INFO : 1169 batches submitted to accumulate stats from 74816 documents (747988 virtual)
2021-04-19 16:11:45,282 : INFO : 1171 batches submitted to accumulate stats from 74944 documents (747684 virtual)
2021-04-19 16:11:46,480 : INFO : 1173 batches submitted to accumulate stats from 75072 documents (746841 virtual)
2021-04-19 16:11:48,870 : INFO : 1180 batches submitted to accumulate stats from 75520 documents (740918 virtual)
2021-04-19 16:11:49,026 : INFO : 1181 batches submitted to accumulate stats from 75584 documents (741109 virtual)
2021-04-19 16:11:52,005 : INFO : 1191 batches submitted to accumulate stats from 76224 documents (734260 virtual)
2021-04-19 16:11:55,002 : INFO : 1200 batches submitted to accumulate stats from 76800 documents (727879 virtual)
2021-04-19 16:11:55,981 : INFO : 1202 batches submitted to accumulate stats from 76928 d

Save the preprocessed data, corpus and dictionary for later exploration  

In [10]:
df.to_csv('data_for_interpretation.csv')

with open('models/corpus.pkl', 'wb') as f:
    pickle.dump(corpus, f)
    
dictionary.save('models/dictionary')

2021-04-19 16:12:47,896 : INFO : saving Dictionary object under models/dictionary, separately None
2021-04-19 16:12:47,900 : INFO : saved models/dictionary
